# LOW CSP Shutdown Sequence

References:
- [LOW.CSP LMC Documentation](https://developer.skatelescope.org/projects/ska-csp-lmc-low/en/latest/lmc/low_csp_lmc.html)
- [LOW.CSP LMC Tango Clients Examples](https://developer.skatelescope.org/projects/ska-csp-lmc-low/en/latest/example/example.html)
- [CSP LMC commands for AA05](https://confluence.skatelescope.org/display/SE/CSP+LMC+commands+for+AA05)
- Currently the test is restricted to testing only a single subarray.

The only deviation noted is that after off() command on subarray, the subarrays healthState should report OK (0), currently this is not implemented and the healthState does not update and remains UNKNOWN (3). Since this is a valid failure from expected behavior it is noted as such in the notebook tests, but the user should note that this failure does not affect the fundamental operation of the LOW CSP and can be safely ignored for the moment.   

### Viewing Tango attributes
The notebook will interrogate device states and report back attribute values as part of the verification output.    
For visual inspection of device attributes the Taranta API interface is used.    
You can access the interface via a web browser by pointing the URL to the appropriate namespace on your k8s cluster    
`http://<k8s_CLUSTER>/<KUBE_NAMESPACE>/taranta/devices/low-csp/`    
e.g. for a deployment on the CLP    
`http://k8s.clp.skao.int/ska-low-csp-baseline/taranta/devices/low-csp/`

### Prerequisites

- All necessary equipment are installed and verified
- Assume a network is available and all equipment/systems are powered
- P4 switch is configured in order to control CBF
- LOW CSP has been deployed to the k8s cluster

### Imports

In [ ]:
import json
import os
import time
from contextlib import suppress
from typing import Any

from ska_control_model import AdminMode, ObsState
from tango import ConnectionFailed, Database, DeviceProxy, DevState

### Tango config

This section links the notebook execution to the tango devices on the cluster and requires user updates when the notebook is run on a system other than the Low Digital PSI in Eindhoven.

Ensure the KUBE_NAMESPACE namespace parameter correctly identifies the k8s namespace with which to intend to interact.

In [ ]:
# specify here the namespace to connect in this cluster
KUBE_NAMESPACE = "ska-low-csp-baseline"
# set the name of the databaseds service
DATABASEDS_NAME = "ska-low-csp-databaseds"

# finally set the TANGO_HOST
os.environ["TANGO_HOST"] = f"{DATABASEDS_NAME}.{KUBE_NAMESPACE}.svc.cluster.local:10000"

### Tango Database

In [ ]:
tango_db = Database()

### Tango proxy devices

In [ ]:
# Low Csp controller
csp_ctl_fqdns = tango_db.get_device_exported_for_class("LowCspController").value_string
print("CSP Controllers:")
print(*[" - " + each for each in csp_ctl_fqdns], sep="\n")
csp_controller = DeviceProxy(csp_ctl_fqdns[0])

# Low Csp subarray
csp_subarr_fqdns = tango_db.get_device_exported_for_class("LowCspSubarray").value_string
print("CSP Subarrays:")
print(*[" - " + each for each in csp_subarr_fqdns], sep="\n")
csp_subarray = DeviceProxy(csp_subarr_fqdns[0])

# Cbf controller
cbf_ctl_fqdns = tango_db.get_device_exported_for_class("LowCbfController").value_string
print("CBF Controllers:")
print(*[" - " + each for each in cbf_ctl_fqdns], sep="\n")
cbf_controller = DeviceProxy(cbf_ctl_fqdns[0])

# Cbf Subarray
cbf_subarr_fqdns = tango_db.get_device_exported_for_class("LowCbfSubarray").value_string
print("CBF Subarrays:")
print(*[" - " + each for each in cbf_subarr_fqdns], sep="\n")
cbf_subarray = DeviceProxy(cbf_subarr_fqdns[0])

CSP Controllers:
 - low-csp/control/0
CSP Subarrays:
 - low-csp/subarray/01
 - low-csp/subarray/02
 - low-csp/subarray/03
 - low-csp/subarray/04
CBF Controllers:
 - low-cbf/control/0
CBF Subarrays:
 - low-cbf/subarray/01
 - low-cbf/subarray/02
 - low-cbf/subarray/03
 - low-cbf/subarray/04


In [ ]:
csp_devices = (csp_controller, csp_subarray)
cbf_devices = (cbf_controller, cbf_subarray)
all_devices = csp_devices + cbf_devices

### Helper functions

In [ ]:
def wait_until(predicate: callable, message_on_fail: str = None, timeout: int = 300, poll_frequency: int = 2) -> None:
    """Wait until statement has a certain value.

    :param predicate: Any callable which returns bool
    :param message_on_fail: Message for the exception on failure
    :param timeout: Approximate time-out period
    :param poll_frequency: wait iterations time
    :raises TimeoutError: if expected condition not seen before timing out
    """
    start = time.time()
    while True:
        try:
            return_val = predicate()
            if return_val:
                return return_val
        except Exception:  # pylint: disable=broad-exception-caught
            time.sleep(0.1)
        if time.time() - start > timeout:
            raise TimeoutError(f"Timeout occurred: {message_on_fail}")
        time.sleep(poll_frequency)


def wait_for_attribute_value(
    device: DeviceProxy,  # pylint: disable = redefined-outer-name
    attribute: str,
    value: Any = True,
    failure_message: str = "Timed out waiting for attribute value",
    timeout_sec: int = 120,
) -> None:
    """
    Wait until an attribute has a certain value.

    :param device: Tango device proxy with the attribute to check
    :param attribute: The name of the attribute
    :param value: Expected value (defaults to True)
    :param failure_message: Message for the exception on failure.
    Defaults to "Timed out waiting for attribute value".
    A note about duration is appended.
    :param timeout_sec: Approximate time-out period  in seconds (in reality
    it could be longer due to delays waiting for each attribute read)
    :raises RuntimeError: if expected value not seen before timing out
    """
    deadline = time.time() + timeout_sec
    poll_interval_seconds = 2
    while time.time() < deadline:
        if device.read_attribute(attribute).value == value:
            break
        time.sleep(poll_interval_seconds)
    else:
        raise RuntimeError(f"{failure_message} after {timeout_sec} sec")


def wait_for_device_response(
    device: DeviceProxy,  # pylint: disable = redefined-outer-name
    failure_message: str = "Timed out waiting for device to respond",
    timeout_sec: int = 120,
) -> None:
    """
    Wait until a device responds.

    :param device: Tango device proxy to wait for
    :param failure_message: Message for the exception on failure.
    Defaults to "Timed out waiting for device to respond".
    A note about duration is appended.
    :param timeout_sec: Approximate time-out period in seconds
    :raises RuntimeError: if the device does not respond in time
    """
    deadline = time.time() + timeout_sec
    poll_interval_seconds = 2
    while time.time() < deadline:
        try:
            device.ping()
            return
        except ConnectionFailed:
            time.sleep(poll_interval_seconds)
    raise RuntimeError(f"{failure_message} after {timeout_sec} sec")


# Coloured printing functions for strings that use universal ANSI escape sequences.
# fail: bold red, pass: bold green, warn: bold yellow,
# info: bold blue, bold: bold white


def print_fail(message, start="", end="\n"):
    """Print coloured fail message"""
    print(f"{start}\x1b[1;31m{message}\x1b[0m", end=end)


def print_pass(message, start="", end="\n"):
    """Print coloured pass message"""
    print(f"{start}\x1b[1;32m{message}\x1b[0m", end=end)


def print_warn(message, start="", end="\n"):
    """Print coloured warn message"""
    print(f"{start}\x1b[1;33m{message}\x1b[0m", end=end)


def print_info(message, start="", end="\n"):
    """Print info message"""
    print(f"{start}{message}", end=end)


def color_print(device: DeviceProxy):  # pylint: disable = redefined-outer-name
    """Print coloured output"""
    wait_for_device_response(device)
    if device.state() == DevState.FAULT:
        print_fail(f"{device.status()}", start="\t")
    elif device.state() == DevState.ALARM:
        print_warn(f"{device.status()}", start="\t")
    else:
        print_info(f"{device.status()}", start="\t")


def show_state():
    """Show state of the devices"""
    for device in all_devices:  # pylint: disable = redefined-outer-name
        print(f"TANGO device: {device.name()}")
        color_print(device)
        try:
            print(f"\t{str(device.adminMode)}")
        except Exception:
            print("raises error in this state")
        print(f"\t{str(device.healthState)}")
        with suppress(AttributeError):
            print(f"\t{str(device.obsState)}")

In [ ]:
show_state()

TANGO device: low-csp/control/0
	The device is in DISABLE state.
	adminMode.OFFLINE
	healthState.UNKNOWN
TANGO device: low-csp/subarray/01
	The device is in DISABLE state.
	adminMode.OFFLINE
	healthState.UNKNOWN
	obsState.EMPTY
TANGO device: low-cbf/control/0
	The device is in DISABLE state.
	adminMode.OFFLINE
	healthState.UNKNOWN
TANGO device: low-cbf/subarray/01
	The device is in DISABLE state.
	adminMode.OFFLINE
	healthState.UNKNOWN
	obsState.EMPTY


### Init devices

**WARNING**:    
Initialisation of the system only happens once after a fresh deployment.    
Only run the cell below if the test is running on a freshly deployed system that has not been initialised yet.
Rerunning Init() on an already deployed system may lead to errors and FAULT conditions

In [ ]:
if csp_controller.adminMode == AdminMode.OFFLINE:
    for device in all_devices:
        print(f"Initializing TANGO device: {device.name()}")
        device.set_timeout_millis(60_000)
        device.Init()

Initializing TANGO device: low-csp/control/0
Initializing TANGO device: low-csp/subarray/01
Initializing TANGO device: low-cbf/control/0
Initializing TANGO device: low-cbf/subarray/01


In [ ]:
if csp_controller.adminMode == AdminMode.OFFLINE:
    csp_controller.adminMode = AdminMode.ONLINE
    wait_for_attribute_value(csp_controller, "isCommunicating", True)

In [ ]:
show_state()

TANGO device: low-csp/control/0
	The device is in ON state.
	adminMode.ONLINE
	healthState.UNKNOWN
TANGO device: low-csp/subarray/01
	The device is in ON state.
	adminMode.ONLINE
	healthState.UNKNOWN
	obsState.EMPTY
TANGO device: low-cbf/control/0
	The device is in ON state.
	adminMode.ONLINE
	healthState.UNKNOWN
TANGO device: low-cbf/subarray/01
	The device is in ON state.
	adminMode.ONLINE
	healthState.UNKNOWN
	obsState.EMPTY


### Assign resources

In [ ]:
print("Assign resources")
# resources can only be assigned if the array is empty
print(f"{csp_subarray.dev_name()} in {str(csp_subarray.obsState)}")
assert csp_subarray.obsState == ObsState.EMPTY

assign_resources_json = {
    "interface": "https://schema.skao.int/ska-low-csp-assignresources/2.0",
    "common": {
        "subarray_id": 1,
    },
    "lowcbf": {},
}
print(assign_resources_json)

Assign resources
low-csp/subarray/01 in obsState.EMPTY
{'interface': 'https://schema.skao.int/ska-low-csp-assignresources/2.0', 'common': {'subarray_id': 1}, 'lowcbf': {}}


In [ ]:
csp_subarray.AssignResources(json.dumps(assign_resources_json))
print("Verify subarray 1 moved from EMPTY to IDLE")
wait_for_attribute_value(csp_subarray, "obsState", ObsState.IDLE, "Assignment not finished")
print(f"{csp_subarray.dev_name()} in {str(csp_subarray.obsState)}")

Verify subarray 1 moved from EMPTY to IDLE
low-csp/subarray/01 in obsState.IDLE


In [ ]:
show_state()

TANGO device: low-csp/control/0
	The device is in ON state.
	adminMode.ONLINE
	healthState.UNKNOWN
TANGO device: low-csp/subarray/01
	The device is in ON state.
	adminMode.ONLINE
	healthState.UNKNOWN
	obsState.IDLE
TANGO device: low-cbf/control/0
	The device is in ON state.
	adminMode.ONLINE
	healthState.UNKNOWN
TANGO device: low-cbf/subarray/01
	The device is in ON state.
	adminMode.ONLINE
	healthState.UNKNOWN
	obsState.IDLE


### Transit LOW CSP to OFF state
OFF: power is disconnected. This state cannot be reported by CSP itself.

The Off command disables any signal processing capability of a subarray and all its allocated resources are also released. As for the ADR-8, this command can be issued fron any observing state.    
https://confluence.skatelescope.org/pages/viewpage.action?pageId=105416556

In [ ]:
csp_subarray.off()
wait_until(
    lambda: "off completed" in csp_subarray.longRunningCommandResult[1],
    "Off is not completed after 300s",
)

True

### Prove OFF command executed on a subarrays

In [ ]:
if csp_subarray.obsState == ObsState.EMPTY:
    print_pass(f"{csp_subarray.name()} is {csp_subarray.obsState.value}/{csp_subarray.obsState.name}")
    print_pass("OFF command on csp subarray executed successfully")
    print_pass("Check passed")
else:
    print_fail(f"{csp_subarray.name()} is {csp_subarray.obsState.value}/{csp_subarray.obsState.name}")
    print_fail("CSP Subarray is not in EMPTY state after off command")
    print_fail("Check failed should be EMPTY")


if csp_subarray.healthState.name == "OK":
    print_pass(f"{csp_subarray.name()} healthState is {csp_subarray.healthState.value}/{csp_subarray.healthState.name}")
    print_pass("Check passed")
else:
    print_fail(f"{csp_subarray.name()} healthState is {csp_subarray.healthState.value}/{csp_subarray.healthState.name}")
    print_fail("Check Failed should be OK")


if cbf_subarray.obsState == ObsState.EMPTY:
    print_pass(f"{cbf_subarray.name()} is {cbf_subarray.obsState.value}/{cbf_subarray.obsState.name}")
    print_pass("OFF command for cbf subarray executed successfully")
    print_pass("Check passed")
else:
    print_fail(f"{cbf_subarray.name()} is {cbf_subarray.obsState.value}/{cbf_subarray.obsState.name}")
    print_fail("CBF Subarray is not in EMPTY state after off command")
    print_fail("Check failed should be EMPTY")


if cbf_subarray.healthState.name == "OK":
    print_pass(f"{cbf_subarray.name()} healthState is {cbf_subarray.healthState.value}/{cbf_subarray.healthState.name}")
    print_pass("Check passed")
else:
    print_fail(f"{cbf_subarray.name()} healthState is {cbf_subarray.healthState.value}/{cbf_subarray.healthState.name}")
    print_fail("Check Failed should be OK")

low-csp/subarray/01 is 0/EMPTY
OFF command on csp subarray executed successfully
Check passed
low-csp/subarray/01 healthState is 3/UNKNOWN
Check Failed should be OK
low-cbf/subarray/01 is 0/EMPTY
OFF command for cbf subarray executed successfully
Check passed
low-cbf/subarray/01 healthState is 3/UNKNOWN
Check Failed should be OK


### TMC commands LOW CSP to adminMode=OFFLINE

In [ ]:
csp_controller.adminMode = AdminMode.OFFLINE
wait_for_attribute_value(csp_controller, "isCommunicating", True)

### LOW CSP devices verification

In [ ]:
if csp_controller.state() == DevState.DISABLE:
    print_pass(f"{csp_controller.name()} state is {csp_controller.state()}")
    print_pass("Check passed")
else:
    print_fail(f"{csp_controller.name()} state is {csp_controller.state()}")
    print_fail("Check Failed should be DISABLED")

if csp_subarray.state() == DevState.DISABLE:
    print_pass(f"{csp_subarray.name()} state is {csp_subarray.state()}")
    print_pass("Check passed")
else:
    print_fail(f"{csp_subarray.name()} state is {csp_subarray.state()}")
    print_fail("Check Failed should be DISABLED")

if cbf_controller.adminmode == AdminMode.OFFLINE:
    print_pass(f"{csp_controller.name()} adminmode is {csp_controller.adminmode.value}/{csp_controller.adminmode.name}")
    print_pass("Check passed")
else:
    print_fail(f"{csp_controller.name()} adminmode is {csp_controller.adminmode.value}/{csp_controller.adminmode.name}")
    print_fail("Check Failed should be OFFLINE")

if cbf_controller.healthState.name == "UNKNOWN":
    print_pass(f"{csp_controller.name()} healthState is {csp_controller.healthState.value}/{csp_controller.healthState.name}")
    print_pass("Check passed")
else:
    print_fail(f"{csp_controller.name()} healthState is {csp_controller.healthState.value}/{csp_controller.healthState.name}")
    print_fail("Check Failed should be UNKNOWN")

low-csp/control/0 state is DISABLE
Check passed
low-csp/subarray/01 state is DISABLE
Check passed
low-csp/control/0 adminmode is 1/OFFLINE
Check passed
low-csp/control/0 healthState is 3/UNKNOWN
Check passed


### LOW CBF devices verification

In [ ]:
if cbf_controller.state() == DevState.DISABLE:
    print_pass(f"{cbf_controller.name()} state is {cbf_controller.state()}")
    print_pass("Check passed")
else:
    print_fail(f"{cbf_controller.name()} state is {cbf_controller.state()}")
    print_fail("Check Failed should be DISABLED")

if cbf_subarray.state() == DevState.DISABLE:
    print_pass(f"{cbf_subarray.name()} state is {cbf_subarray.state()}")
    print_pass("Check passed")
else:
    print_fail(f"{cbf_subarray.name()} state is {cbf_subarray.state()}")
    print_fail("Check Failed should be DISABLED")

if cbf_controller.adminmode == AdminMode.OFFLINE:
    print_pass(f"{cbf_controller.name()} adminmode is {cbf_controller.adminmode.value}/{cbf_controller.adminmode.name}")
    print_pass("Check passed")
else:
    print_fail(f"{cbf_controller.name()} adminmode is {cbf_controller.adminmode.value}/{cbf_controller.adminmode.name}")
    print_fail("Check Failed should be OFFLINE")

if cbf_controller.healthState.name == "UNKNOWN":
    print_pass(f"{cbf_controller.name()} healthState is {cbf_controller.healthState.value}/{cbf_controller.healthState.name}")
    print_pass("Check passed")
else:
    print_fail(f"{cbf_controller.name()} healthState is {cbf_controller.healthState.value}/{cbf_controller.healthState.name}")
    print_fail("Check Failed should be UNKNOWN")

low-cbf/control/0 state is DISABLE
Check passed
low-cbf/subarray/01 state is DISABLE
Check passed
low-cbf/control/0 adminmode is 1/OFFLINE
Check passed
low-cbf/control/0 healthState is 3/UNKNOWN
Check passed
